<a href="https://colab.research.google.com/github/cristina-ramos/class_NLP/blob/main/Research/Data_Aug.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Loading in the dataset I will be using: The Multilingual Amazon Review Corpus

In [ ]:
import pandas as pd
import numpy as np
import nltk
import spacy
import matplotlib.pyplot as plt
import random
from numpy import mean, array

In [ ]:
!python -m spacy download es_core_news_sm

In [ ]:
pip install datasets

In [ ]:
pip install nlp

In [ ]:
nltk.download('omw')
nltk.download('punkt')

[nltk_data] Downloading package omw to /root/nltk_data...
[nltk_data]   Unzipping corpora/omw.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
from nltk.corpus import stopwords
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [ ]:
pip install numpy requests nlpaug

In [ ]:
pip install transformers

In [ ]:
import es_core_news_sm
nlp = es_core_news_sm.load()

In [ ]:
from datasets import load_dataset, Dataset

dataset = load_dataset("amazon_reviews_multi", 'es', split='test')

In [ ]:
import nlpaug.augmenter.char as nac
import nlpaug.augmenter.word as naw
import nlpaug.augmenter.sentence as nas
import nlpaug.flow as nafc
from nlpaug.util import Action

In [ ]:
from nltk.tokenize import word_tokenize

Using Pandas to create DataFrame

In [ ]:
df = pd.DataFrame(data=dataset, columns=['review_id','product_id','reviewer_id','stars','review_body','review_title','language','product_category'])
df = df[df["stars"].notnull()]
df = df.sample(frac=1)
df

review_id          product_id  ... language  product_category
2761  es_0380368  product_es_0329053  ...       es           apparel
2088  es_0836952  product_es_0490219  ...       es                pc
2298  es_0489188  product_es_0309980  ...       es      pet_products
3905  es_0025950  product_es_0821511  ...       es           luggage
493   es_0249852  product_es_0916508  ...       es               toy
...          ...                 ...  ...      ...               ...
4670  es_0308295  product_es_0221604  ...       es         drugstore
3291  es_0346447  product_es_0157455  ...       es          wireless
2059  es_0861338  product_es_0470601  ...       es              home
2051  es_0272973  product_es_0511617  ...       es             watch
160   es_0611438  product_es_0754226  ...       es           kitchen

[5000 rows x 8 columns]

In [ ]:
import string

df['Word Count'] = [len(review.split()) for review in df['review_body']]

df['Uppercase Char Count'] = [sum(char.isupper() for char in review) \
                              for review in df['review_body']]                           

df['Special Char Count'] = [sum(char in string.punctuation for char in review) \
                            for review in df['review_body']] 

df

review_id          product_id  ... Uppercase Char Count  Special Char Count
2761  es_0380368  product_es_0329053  ...                    4                   7
2088  es_0836952  product_es_0490219  ...                    2                   3
2298  es_0489188  product_es_0309980  ...                    1                   1
3905  es_0025950  product_es_0821511  ...                    1                   0
493   es_0249852  product_es_0916508  ...                    1                   0
...          ...                 ...  ...                  ...                 ...
4670  es_0308295  product_es_0221604  ...                    0                   6
3291  es_0346447  product_es_0157455  ...                    4                   7
2059  es_0861338  product_es_0470601  ...                    4                   3
2051  es_0272973  product_es_0511617  ...                    1                   0
160   es_0611438  product_es_0754226  ...                    0                   2

[5000 rows x 11 columns]

In [ ]:
df2 = df.drop(['review_id', 'product_id', 'reviewer_id'], axis=1)

In [ ]:
neg = df2[df2['stars'] <= 3]
print(neg)
pos = df2[df2['stars'] >= 4]
print(pos)

      stars  ... Special Char Count
2761      3  ...                  7
2088      3  ...                  3
2298      3  ...                  1
493       1  ...                  0
1587      2  ...                  2
...     ...  ...                ...
473       1  ...                  3
1563      2  ...                  4
2059      3  ...                  3
2051      3  ...                  0
160       1  ...                  2

[3000 rows x 8 columns]
      stars  ... Special Char Count
3905      4  ...                  0
4526      5  ...                 14
4211      5  ...                  3
3368      4  ...                  6
3488      4  ...                  3
...     ...  ...                ...
3055      4  ...                  0
3949      4  ...                  2
4911      5  ...                  1
4670      5  ...                  6
3291      4  ...                  7

[2000 rows x 8 columns]


In [ ]:
from collections import Counter

def getMostCommonWords(reviews, n_most_common, stopwords=None):
    flattened_reviews = [word for review in reviews for word in \
                         review.lower().split()]

    flattened_reviews = [''.join(char for char in review if \
                                 char not in string.punctuation) for \
                         review in flattened_reviews]
    if stopwords:
        flattened_reviews = [word for word in flattened_reviews if \
                             word not in stopwords]

    flattened_reviews = [review for review in flattened_reviews if review]

    return Counter(flattened_reviews).most_common(n_most_common)

In [ ]:
getMostCommonWords(pos['review_body'], 10, stopwords.words('spanish'))

[('bien', 621),
 ('calidad', 353),
 ('buena', 319),
 ('precio', 305),
 ('buen', 239),
 ('producto', 237),
 ('si', 190),
 ('bastante', 176),
 ('perfecto', 175),
 ('cumple', 133)]

In [ ]:
getMostCommonWords(neg['review_body'], 10, stopwords.words('spanish'))

[('bien', 642),
 ('si', 437),
 ('calidad', 392),
 ('producto', 389),
 ('precio', 257),
 ('dos', 223),
 ('mal', 189),
 ('bastante', 185),
 ('solo', 169),
 ('mas', 165)]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(min_df=15)
bow = vectorizer.fit_transform(df2['review_body'])
labels = df2['stars']
len(vectorizer.get_feature_names())

920

In [ ]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(bow, labels, test_size=0.33)
from sklearn.ensemble import RandomForestClassifier as rfc

In [ ]:
classifier = rfc()
classifier.fit(X_train,y_train)
classifier.score(X_test,y_test)

0.4206060606060606

In [ ]:
print(dataset)
print(dataset.shape, dataset.column_names, dataset.features)

Dataset({
    features: ['review_id', 'product_id', 'reviewer_id', 'stars', 'review_body', 'review_title', 'language', 'product_category'],
    num_rows: 5000
})
(5000, 8) ['language', 'product_category', 'product_id', 'review_body', 'review_id', 'review_title', 'reviewer_id', 'stars'] {'review_id': Value(dtype='string', id=None), 'product_id': Value(dtype='string', id=None), 'reviewer_id': Value(dtype='string', id=None), 'stars': Value(dtype='int32', id=None), 'review_body': Value(dtype='string', id=None), 'review_title': Value(dtype='string', id=None), 'language': Value(dtype='string', id=None), 'product_category': Value(dtype='string', id=None)}


In [ ]:
pos_reviews = pos['review_body']
neg_reviews = neg['review_body']
reviews = df2['review_body']
print(len(pos_reviews))
print(len(neg_reviews))
print(len(reviews))

2000
3000
5000


In [ ]:
reviews.dropna()

2761    Pues el pantalón es muy corriente, pero x el p...
2088    Esta buen, queda bien en el ordenador lo deja ...
2298      Práctica pero le falta que el suelo sea rígido.
3905    El tejido parece fuerte y están chulos los det...
493     Son malos apenas pinta acaban de llegar y lo e...
                              ...                        
4670    hace tiempo he comprado la maquinita de fuma,p...
3291    La funda encaja perfectamente. Está bien acaba...
2059    Alumbran bien. Pero la cinta adhesiva pega muy...
2051                   Es de peor calidad que la original
160     no me ha gustado nada, me lo cobraron y no lo ...
Name: review_body, Length: 5000, dtype: object

In [ ]:
pos_sentences = []
for i in pos_reviews:
  split_lines = i.split("',")
  pos_sentences.append(split_lines)

neg_sentences = []
for i in neg_reviews:
  split_lines = i.split("',")
  neg_sentences.append(split_lines)

sentences = []
for i in reviews:
  split_lines = i.split("',")
  sentences.append(split_lines)

synonym augmentation:

In [ ]:
syn_aug_texts = []
for s in sentences:
  aug = naw.SynonymAug(aug_src='wordnet', lang='spa')
  augmented_text = aug.augment(s)
  syn_aug_texts.append(augmented_text)

In [ ]:
print("Original Text:")
print(sentences, '\n')
print("Augmented Text:")
print(syn_aug_texts, '\n')

Original Text:
[['Pues el pantalón es muy corriente, pero x el precio no puedes pedir más. La talla un disparate enano. En lugar de devolverlo me ofrecieron enviar otro. Aún no ha llegado así q...'], ['Esta buen, queda bien en el ordenador lo deja muy protegido pero la calidad del plástico se ve que no es muy buena y que en sí no parece madera de verdad ni anda cerca de parecerlo. También tengo que decir que la carcasa que me vino es diferente a la de la foto esta es más clarita.'], ['Práctica pero le falta que el suelo sea rígido.'], ['El tejido parece fuerte y están chulos los detalles q trae la mochila lo único q falla es q no lleva base dura y tendré q ponérsela de otra mochila xq para cargar libros no me fio sin base'], ['Son malos apenas pinta acaban de llegar y lo estamos probando son para regalar a los compis del cumple pero no si quieran pintan vienen como seca la tinta'], ['Me ha parecido una compra muy útil y buena. Quería un reloj que contase los pasos y calorías gastadas y

random character:

In [ ]:
char_aug_texts = []
for s in sentences:
  aug = nac.RandomCharAug(action='insert')
  augmented_char = aug.augment(s)
  char_aug_texts.append(augmented_char)

In [ ]:
print("Orginal Text:")
print(sentences, '\n')
print("Character Augmentation:")
print(char_aug_texts, '\n')

Orginal Text:
[['Pues el pantalón es muy corriente, pero x el precio no puedes pedir más. La talla un disparate enano. En lugar de devolverlo me ofrecieron enviar otro. Aún no ha llegado así q...'], ['Esta buen, queda bien en el ordenador lo deja muy protegido pero la calidad del plástico se ve que no es muy buena y que en sí no parece madera de verdad ni anda cerca de parecerlo. También tengo que decir que la carcasa que me vino es diferente a la de la foto esta es más clarita.'], ['Práctica pero le falta que el suelo sea rígido.'], ['El tejido parece fuerte y están chulos los detalles q trae la mochila lo único q falla es q no lleva base dura y tendré q ponérsela de otra mochila xq para cargar libros no me fio sin base'], ['Son malos apenas pinta acaban de llegar y lo estamos probando son para regalar a los compis del cumple pero no si quieran pintan vienen como seca la tinta'], ['Me ha parecido una compra muy útil y buena. Quería un reloj que contase los pasos y calorías gastadas y 

contextual word embeddings: this takes the longest to load (over 2 hours)


In [ ]:
emb_aug_texts = []
for s in sentences:
  aug = naw.ContextualWordEmbsAug(model_path='bert-base-multilingual-uncased', aug_p=0.1)
  augmented_word = aug.augment(s)
  emb_aug_texts.append(augmented_word)

In [ ]:
print("Original Text:")
print(sentences, '\n')
print("Embedding Augmentations: ")
print(emb_aug_texts)

Original Text:
[['no me llego el articulo me lo mando por correos normal sin seguimiento y nunca me llego tota un desastre'], ['la mensajería horrible, no compro mas'], ['Estoy muy decepcionado con el vendedor ya que el pedido no me llegó a tiempo y no cumplió los plazos de envío y era una cosa que necesitaba urgente. Para colmo me pongo en contacto con el vendedor y no da señales. No recomiendo nada'], ['Mi valoración no es sobre el producto sino sobre AMAZON. Ofrecéis el producto a 299€ y tras varios días me devolvéis el dinero porque os habéis equivocado en el anuncio, según vosotros, ahora es 399€. Es la primera vez que me ocurre esto. Cuando he comprado en cualquier sitio y el precio marcado no se correspondía con el valor de caja siempre me lo han vendido con el precio marcado. Es inverosímil lo ocurrido, pero la ultima palabra me la dará la oficina del consumidor'], ['Pues tenía interés en este libro y probé la versión kindle. se abre la portada pero nada más. parece una mala br

In [ ]:
print(sentences[19])
print(emb_aug_texts[19])

['Las medidas y las fotos engañan, es para casitas de muñecas para mi hija,hay que arrodillarse para lavarse la cara']
['las medidas y las partes enganan, es tambien casitas de ropa para mi hija, hay que arrodillarse para lavarse la cara']


Antonym Augmentation"

In [ ]:
rand_aug_texts = []
for s in sentences:
  aug = naw.AntonymAug(lang='spa')
  rand_augment = aug.augment(s)
  rand_aug_texts.append(rand_augment)

In [ ]:
print("Orginal Text:")
print(sentences, '\n')
print("Random Augmentation:")
print(rand_aug_texts, '\n')

Orginal Text:
[['Pues el pantalón es muy corriente, pero x el precio no puedes pedir más. La talla un disparate enano. En lugar de devolverlo me ofrecieron enviar otro. Aún no ha llegado así q...'], ['Esta buen, queda bien en el ordenador lo deja muy protegido pero la calidad del plástico se ve que no es muy buena y que en sí no parece madera de verdad ni anda cerca de parecerlo. También tengo que decir que la carcasa que me vino es diferente a la de la foto esta es más clarita.'], ['Práctica pero le falta que el suelo sea rígido.'], ['El tejido parece fuerte y están chulos los detalles q trae la mochila lo único q falla es q no lleva base dura y tendré q ponérsela de otra mochila xq para cargar libros no me fio sin base'], ['Son malos apenas pinta acaban de llegar y lo estamos probando son para regalar a los compis del cumple pero no si quieran pintan vienen como seca la tinta'], ['Me ha parecido una compra muy útil y buena. Quería un reloj que contase los pasos y calorías gastadas y 

Random Deletion:

In [ ]:
del_aug_texts = []
for s in sentences:
  aug = naw.RandomWordAug()
  augment_del = aug.augment(s)
  del_aug_texts.append(augment_del)

In [ ]:
print("Orginal Text:")
print(sentences, '\n')
print("Random Augmentation:")
print(del_aug_texts, '\n')

Orginal Text:
[['Pues el pantalón es muy corriente, pero x el precio no puedes pedir más. La talla un disparate enano. En lugar de devolverlo me ofrecieron enviar otro. Aún no ha llegado así q...'], ['Esta buen, queda bien en el ordenador lo deja muy protegido pero la calidad del plástico se ve que no es muy buena y que en sí no parece madera de verdad ni anda cerca de parecerlo. También tengo que decir que la carcasa que me vino es diferente a la de la foto esta es más clarita.'], ['Práctica pero le falta que el suelo sea rígido.'], ['El tejido parece fuerte y están chulos los detalles q trae la mochila lo único q falla es q no lleva base dura y tendré q ponérsela de otra mochila xq para cargar libros no me fio sin base'], ['Son malos apenas pinta acaban de llegar y lo estamos probando son para regalar a los compis del cumple pero no si quieran pintan vienen como seca la tinta'], ['Me ha parecido una compra muy útil y buena. Quería un reloj que contase los pasos y calorías gastadas y 

Sentiment Classification:

In [ ]:
from textblob import TextBlob
from textblob.sentiments import NaiveBayesAnalyzer

In [ ]:
doc = nlp(str(reviews))

Original Scores

In [ ]:
analysis = TextBlob(str(sentences)).sentiment
print("Overall Sentiment Scores for Original Reviews:", analysis)

Overall Sentiment Scores for Original Reviews: Sentiment(polarity=0.15113291753363947, subjectivity=0.6540227242948854)


Synonym Scores

In [ ]:
analysis_syn = TextBlob(str(syn_aug_texts)).sentiment
print("Overall Sentiment Scores for Synonym Augmentations:", analysis_syn)

Overall Sentiment Scores for Synonym Augmentations: Sentiment(polarity=0.1427530820321372, subjectivity=0.6488650827021074)


Character Scores

In [ ]:
analysis_char = TextBlob(str(char_aug_texts)).sentiment
print("Overall Sentiment Scores for Character Augmentations:", analysis_char)

Overall Sentiment Scores for Character Augmentations: Sentiment(polarity=0.19920663644609554, subjectivity=0.6398726987298423)


Deletion Scores

In [ ]:
analysis_del = TextBlob(str(del_aug_texts)).sentiment
print("Overall Sentiment Scores for Deletion Augmentations:", analysis_del)

Overall Sentiment Scores for Deletion Augmentations: Sentiment(polarity=0.15208596586173886, subjectivity=0.64708350767469)


Antonym Scores

In [ ]:
analysis_ant = TextBlob(str(rand_aug_texts)).sentiment
print("Overall Sentiment Scores for Antonym Augmentations:", analysis_ant)

Overall Sentiment Scores for Antonym Augmentations: Sentiment(polarity=0.03422698173306065, subjectivity=0.5838904514133031)


Embedding Scores:

In [ ]:
analysis_emb = TextBlob(str(emb_aug_texts)).sentiment
print("Overall Sentiment Scores for Embedding Augmentation:", analysis_emb)

Overall Sentiment Scores for Embedding Augmentation: Sentiment(polarity=0.1536803838929627, subjectivity=0.6236243876605321)


Another approach to sentiment classification using Hugging Face:

In [ ]:
from transformers import pipeline

In [ ]:
classifier = pipeline('sentiment-analysis', model='nlptown/bert-base-multilingual-uncased-sentiment')

In [ ]:
results = []
for s in sentences:
  res = classifier(s)
  results.append(res)

In [ ]:
import statistics
print(results)

[[{'label': '1 star', 'score': 0.44784799218177795}], [{'label': '3 stars', 'score': 0.6561962962150574}], [{'label': '3 stars', 'score': 0.638704776763916}], [{'label': '3 stars', 'score': 0.3796842396259308}], [{'label': '1 star', 'score': 0.6515889763832092}], [{'label': '5 stars', 'score': 0.6025416851043701}], [{'label': '2 stars', 'score': 0.43445053696632385}], [{'label': '2 stars', 'score': 0.4964621365070343}], [{'label': '3 stars', 'score': 0.4964854419231415}], [{'label': '2 stars', 'score': 0.5225644707679749}], [{'label': '3 stars', 'score': 0.6285918951034546}], [{'label': '2 stars', 'score': 0.5033692717552185}], [{'label': '1 star', 'score': 0.5462542772293091}], [{'label': '2 stars', 'score': 0.43303295969963074}], [{'label': '4 stars', 'score': 0.6104947924613953}], [{'label': '1 star', 'score': 0.5021309852600098}], [{'label': '5 stars', 'score': 0.6320890188217163}], [{'label': '3 stars', 'score': 0.6631799340248108}], [{'label': '2 stars', 'score': 0.59297049045562

In [ ]:
df3 = pd.DataFrame(results, columns=['label'])
df3

label
0     {'label': '1 star', 'score': 0.44784799218177795}
1     {'label': '3 stars', 'score': 0.6561962962150574}
2      {'label': '3 stars', 'score': 0.638704776763916}
3     {'label': '3 stars', 'score': 0.3796842396259308}
4      {'label': '1 star', 'score': 0.6515889763832092}
...                                                 ...
4995  {'label': '2 stars', 'score': 0.2738446593284607}
4996  {'label': '3 stars', 'score': 0.5310989618301392}
4997  {'label': '3 stars', 'score': 0.6457688808441162}
4998  {'label': '2 stars', 'score': 0.44441792368888...
4999   {'label': '1 star', 'score': 0.9222561717033386}

[5000 rows x 1 columns]

In [ ]:
df3.label.str.split(expand=True,)
df3

label
0     {'label': '1 star', 'score': 0.44784799218177795}
1     {'label': '3 stars', 'score': 0.6561962962150574}
2      {'label': '3 stars', 'score': 0.638704776763916}
3     {'label': '3 stars', 'score': 0.3796842396259308}
4      {'label': '1 star', 'score': 0.6515889763832092}
...                                                 ...
4995  {'label': '2 stars', 'score': 0.2738446593284607}
4996  {'label': '3 stars', 'score': 0.5310989618301392}
4997  {'label': '3 stars', 'score': 0.6457688808441162}
4998  {'label': '2 stars', 'score': 0.44441792368888...
4999   {'label': '1 star', 'score': 0.9222561717033386}

[5000 rows x 1 columns]